In [165]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.by import By
import numpy as np
import pandas as pd
import time
import re
from multiprocessing import Pool
from functools import partial
from datetime import datetime, timedelta
import os.path
import os
from pymongo import MongoClient 
import pandas as pd 
import json
from pymongo import errors 
from django.core.validators import URLValidator
from django.core.exceptions import ValidationError
from pymongo.errors import BulkWriteError
from tempfile import NamedTemporaryFile
import string
import random
from urllib import request
from bs4 import BeautifulSoup
from urllib.parse import urljoin
from yelp_uri.encoding import recode_uri
import traceback

class IndeedMongodbDao:
    def __init__(self):
        self.conn = MongoClient() 
        self.db = self.conn.Indeed
        self.collection = self.db.data
        self.collection_duplicate_data = self.db.duplicate_data
        
    def _valid_url_format(self,url):
        val = URLValidator()
        try:
            val(url)
        except ValidationError as e:
            raise Exception('bad format for url {}'.format(ur))
    
    def insert_data_bulk(self,data):
        try:
            self.collection.insert_many(data)
        except BulkWriteError as bwe:
            print(bwe.details)
            print(bwe.details['writeErrors'])
            raise
    
    
    def insert_to_dulicate_data(self,url):
        try:
            if url == "":
                raise Exception('url cannot be empty {}'.format(ur))

            self._valid_url_format(url)

            line_to_insert = {"url": url}

            result = self.collection_duplicate_data.insert_one(line_to_insert) 
        except Exception as e:
            print(e)
        
    
    def insert_data(self, url, title, name, address, publication_date,salaire, description, localisation):
        
        try:
            if url == "":
                raise Exception('url cannot be empty {}'.format(ur))

            self._valid_url_format(url)

            if title == "":
                raise Exception('title cannot be empty {}'.format(title))

            if name == "":
                raise Exception('the name of company cannot be be empty {}'.format(title))

            if description == "":
                raise Exception('description of company cannot be be empty {}'.format(title))

            line_to_insert = {
                                "url": url,
                                "titre":title,
                                "nom_entreprise":name,
                                "adresse":address,
                                "date_de_publication":publication_date,
                                "salaire":salaire,
                                "description":description,
                                "localisation":localisation
                             }

            # Insert Data 
            result = self.collection.insert_one(line_to_insert) 
        except Exception as e:
            print(e)
    
    def get_all_data(self):
        data = self.collection.find({})
        return data
    
    def description_exist(self, description):
        return self.collection.find({"description" : description}).count() > 0
        
    def url_exist(self, url):
        return self.collection.find({"url" : url}).count() > 0
    
    def url_exist_on_duplicate_data(self, url):
        return self.collection_duplicate_data.find({"url" : url}).count() > 0
    
    def get_all_duplicate(self):
        return self.collection.aggregate([{"$group" : { "_id": "$url", "count": { "$sum": 1 } }}, {"$match": {"_id" :{ "$ne" : None } , "count" : {"$gt": 1} } }, {"$project": {"u" : "$_id", "_id" : 0}}])
    
    def update_salary(self,id, salaire):
        self.collection.update_one({'_id': id},{'$set': {'salaire': salaire}}, upsert=False)

class KeyWordsProvider:
    
    def get_langages(self):
        return ['python', 'r','vba', 'mysql','excel','asp.net','nosql','sql','linux','mongodb',
            'mariadb','java','javascript','php','html','css','sas','c#','ruby','swift','objective-c',
            'vb.net','kotlin','scala','bash','powershell','shell','front end','back end','soap',
            'dasl', 'pict', 'rexx', 'd', 'asp.net', 'f#', 'joy', 'sr', 'back end', 'poplog', 
            'modula-2', 'powershell', 'bash', 'concurrent pascal', 'apl', 'eiffel', 'lisp', 
            'cilk', 'c', 'awk', 'charity', 'bliss', 'spin', 'swift', 'visual basic', 'game maker language',
            'lisaac', 'xl', 'nosql', 'limbo', 'e', 'lava', 'slate', 'revolution', 'coldfusion', 
            'matlab', 'vb.net', 'cobol', 'tcl', 'rpg', 'sas', 'curl', 'front end', 'nemerle', 'f-script', 
            'xml', 's-lang', 'curry', 'basic', 'autoit', 'prolog', 'erlang', 'maya embedded language', 
            'frink', 'oz', 'windows powershell', 'beta', 'moo', 'object-z', 'self', 'leda', 'fortran', 
            'smalltalk', 'afnix', 'mysql', 'm', 'turing', 'jovial', 'lua', 'mondrian', 'io', 'salsa', 
            'kotlin', 'css', 'xotcl', 'perl', 'component pascal', 'mongodb', 'xhtml', 'dibol', 'oberon',
            'ada', 'visual foxpro', 'clist', 'pl/c', 'algol', 'mariadb', 'sql', 'pliant', 'excel', 
            'cobra', 'occam', 'obliq', 'prograph', 'chuck', 'pl/i', 'hypertalk', 'forth', 'ici', 
            'vba', 'beanshell', 'sgml', 'soap', 'opal', 'small', 'pascal', 'applescript', 'roop', 
            'agora', 'moto', 'rapira', 'alf', 'r', 'ml', 'javascript', 'pcastl', 'abcl', 'postscript', 
            'oxygene', 'cecil', 'clean', 'ops5', 'c++', 'shell', 'haskell', 'kite', 'cleo', 'q', 'linux', 
                'vbscript', 'joule', 'rebol', 'jass', 'j', 'fril']
    
    def get_tools(self):
        return ['tableau', 'powerbi','symfony', 'jquery','angular','react','react native','node js','git','github',
            'visual studio','django','flask','api rest','laravel', 'hololens', 'docker', 'jira', 'scrum', 'kanban', 
               'azure','aws', 'teamcity', 'jenkins']
    
    def get_others(self):
        return ['cisco','intel','android','ios','unity', 'Unreal Engine', 'UX Designer','realite virtuelle','realite augmentée','Game','IHM','VR','AR','3D','electronic','iot']

class IndeedItemParser:
    def __init__(self):
        self.driverPath = "C:\\Users\\User\\Documents\\selenium\\driver\\chromedriver.exe"
        self.salary_pattern = "[[S|s]alaire?[\s+]?:?[\s+]?(.*)e?[\s+]?\/(an|mois)|((.*)?[\s+]?par?[\s+]?(an|ans|mois|jour|heure))"
        
    def _get_title(self, soup):
        try:
            #title = driver.find_element_by_xpath("//*[@class='jobsearch-DesktopStickyContainer']//h3")
            title = soup.select(".jobsearch-DesktopStickyContainer h3")
            if len(title) > 0:
                return title[0].text
        except Exception as e:
            print(traceback.format_exc())
        return np.nan
    
    def _get_name(self, soup):
        
        try:    
            #name = driver.find_element_by_xpath("//*[contains(@class,'jobsearch-InlineCompanyRating')]//div[1]")
            name = soup.select("*[class*='jobsearch-InlineCompanyRating'] div")
            if len(name) > 0:
                return name[0].text
        except Exception as e:
            print(traceback.format_exc())
        return np.nan
        
    
    def _get_address(self,soup):
         try:   
            #address = driver.find_element_by_xpath("//*[contains(@class,'jobsearch-InlineCompanyRating')]//div[3]")
            address = soup.select("*[class*='jobsearch-InlineCompanyRating'] div")
            if address[2].text == "-":
                #address = driver.find_element_by_xpath("//*[contains(@class,'jobsearch-InlineCompanyRating')]//div[4]")
                return address[3].text
            return address[2].text
         except Exception as e:
                #address = driver.find_element_by_xpath("//span[@class='jobsearch-JobMetadataHeader-iconLabel'][1]")
                address = soup.select("*[class*='jobsearch-JobMetadataHeader-iconLabel']")
                if len(address) > 0:
                    return address[0].text
                return np.nan
         
        
    def _get_salary_result(self,select_result):
        salary = np.nan
        for item in select_result:
            if "€" in item.text:
                outer_salary = re.compile(self.salary_pattern)
                m_salary = outer_salary.search(item.text)
                if m_salary is not None:
                    salary = m_salary.group(0)
                    break
        return salary

    def _get_salary(self,soup, url):
        try:
            #page = request.urlopen(url)
            #soup = BeautifulSoup(source)
            result = soup.select(".jobsearch-JobMetadataHeader-item")
            if len(result) > 0:
                return self._get_salary_result(result)

            result = soup.select(".jobsearch-JobMetadataHeader-itemWithIcon .jobsearch-JobMetadataHeader-iconLabel")
            if len(result) > 0:
                return self._get_salary_result(result)

            result = soup.select("#jobDescriptionText")
            if len(result) > 0:
                index = index + 1 
                outer_salary = re.compile(self.salary_pattern)
                m_salary = outer_salary.search(result[0].text)
                if m_salary is not None:
                    return self._get_salary_result(m_salary.group(0))
        
        except Exception as e:
            print(traceback.format_exc())
        return np.nan
    
    def _get_description(self,soup):
        try:
            #jobDescriptionText
            #e_description = driver.find_element_by_id("jobDescriptionText")
            e_description = soup.select("#jobDescriptionText")
            if (len(e_description) > 0):
                return e_description[0].text
            return np.nan
        except Exception as e:
            print(traceback.format_exc())
    
    def _get_date(self,soup,url,name):
        #if name == np.nan:
        #    return np.nan
        try:
            #date_str = driver.find_element_by_xpath("//*[@class='jobsearch-JobMetadataFooter']")
            date = datetime.now()
            date_str = soup.select(".jobsearch-JobMetadataFooter")
            date_str_full = date_str[0].text.strip()
            
            re_pattern_count = re.compile(r"\s.*?(\d+\+)\s.*|\s.*?(\d+)\s.*")
            re_pattern_count = re_pattern_count.search(date_str_full)
            if re_pattern_count.group(2) != None:
                count = re_pattern_count.group(2).replace("+","")
            else: 
                count = re_pattern_count.group(1).replace("+","")
            
            if count == "30+":
                return date - timedelta(days=30)
            
            count = int(count)
            re_pattern_label = re.compile(r"\s.*?(jour|jours|heur|heurs|mois|an)")
            re_pattern_label = re_pattern_label.search(date_str_full)
            label = re_pattern_label.group(1)
            print("label -", label,"count -: ", count)
            
            if "jour" in label:
                date = date - timedelta(days=count)
            elif "heur" in label:
                date = date - timedelta(hours=count)
            return date;
        except Exception as e:
            print(traceback.format_exc())
    
    
    def parse(self,url):
        #driver = webdriver.Chrome(self.driverPath)
        #driver.get(url)
        #driver.maximize_window()
        print("page item ",url)
        page = request.urlopen(url)
        soup = BeautifulSoup(page)
        
        #source = driver.page_source
        title = self._get_title(soup)
        name = self._get_name(soup)
        if name == np.nan:
            print("name missing")
        address = self._get_address(soup)
        date = self._get_date(soup, url,name)
        description = self._get_description(soup)
        salaire = self._get_salary(soup,url)
        
        return title, name, address, date, salaire, description


class IndeedPaser:
    def __init__(self):
        self.website = "https://www.indeed.fr"
        self.driverPath = "C:\\Users\\User\\Documents\\selenium\\driver\\chromedriver.exe"
        self.dao = IndeedMongodbDao()
        
        self.jobs = ["developpeur", "data scientist", "data analyst", "business intelligence"]
        self.locations = ["Lyon", "Toulouse", "Nantes", "Bordeaux","Paris"]
        self.indeed_item_parser = IndeedItemParser()
        self.keyWordsProvider = KeyWordsProvider()
    
    def _get_pages_counts(self,soup):
        searchCountPages = None
        try:
            #searchCountPages_elt = driver.find_element_by_id("searchCountPages")
            searchCountPages_elt = soup.select("#searchCountPages")
            if len(searchCountPages_elt) > 0:
                searchCountPages = searchCountPages_elt[0].text.strip().split()
        except Exception as e: 
            print(traceback.format_exc())
        
        if searchCountPages != None:    
            if len(searchCountPages) == 6:
                searchCountPages = int("{0}{1}".format(searchCountPages[3],searchCountPages[4])) 
            else :
                searchCountPages = searchCountPages[3] 
            result = (int(searchCountPages) // 18)

            if result == 1:
                result = 2
            return result
    
    def _get_subs_collections(self,items, nbr=5):
        result = []
        sub = []
        for index, item in enumerate(items):
            sub.append(item)
            if (index > 0) & (index % nbr) == 0:
                result.append(sub)
                sub = []
        return result
    
    def _local_parse_page(self, item_link,localisation):
        try:
            if self.dao.url_exist(item_link) == True:
                print("aready parsed, skip")
            elif self.dao.url_exist_on_duplicate_data(item_link) == True:
                print("duplicate url and aready parsed, skip")
            else:
                title, name, address, date,salaire, description = self.indeed_item_parser.parse(item_link)
                if self.dao.description_exist(description) == True:
                    self.dao.insert_to_dulicate_data(item_link)
                    print("duplicate. archived and skip.")
                    return
                if date == np.nan:
                    print("date nan - ", item_link)
                
                if (item_link != np.nan) & (title != np.nan) & (name != np.nan) & (address != np.nan) & (description != np.nan):
                    self.dao.insert_data(item_link,title,name,address,date,salaire,description,localisation)
                    print("saved :",item_link)   
                    print(salaire)
                
                #self.create_local_file(item_link, source)
        except Exception as e:
            print(traceback.format_exc())
    
    def randomString(self, stringLength=10):
        letters = string.ascii_lowercase
        return ''.join(random.choice(letters) for i in range(stringLength))
                    
    def create_local_file(self, item_link, source):
        file = open("pages/{0}.html".format(self.randomString()), "w")
        source = item_link + "----------------" + source
        file.write(source)
        file.close()
                    
    def parse(self):
        
        for job in self.jobs:
            jobs_filter_list = [job]
            
            if job == "developpeur":
                all_competences = self.keyWordsProvider.get_langages() + self.keyWordsProvider.get_tools() + self.keyWordsProvider.get_others()
                jobs_filter_list = ["{0} {1}".format(job, item) for item in all_competences]
            
            random.shuffle(jobs_filter_list)
            for job_key_word in jobs_filter_list:
                for location in self.locations:

                    query = recode_uri("https://www.indeed.fr/jobs?q={0}&l={1}".format(job_key_word, location))
                    print(query)
                    #browser.get(query)
                    page = request.urlopen(query)
                    soup = BeautifulSoup(page)
                    
                    pages_count = self._get_pages_counts(soup)
                    if pages_count == None:
                        print("No data on {0}, skip".format(query))
                        continue
                    
                    for page_index in random.sample(range(0, pages_count), pages_count):
                        full_query = recode_uri("{0}&start={1}".format(query,page_index))
                        #browser.get(full_query)
                        
                        item_page = request.urlopen(full_query)
                        item_soup = BeautifulSoup(item_page)
                        items = item_soup.select("a[class*='jobtitle']")
                        #items = browser.find_elements_by_xpath("//*[contains(@class,'clickcard')]//*[contains(@class,'jobtitle')]")
                        items = [urljoin(self.website, item["href"]) for item in  items]
                        
                        for index_i, link in enumerate(items):
                            self._local_parse_page(link, location)

In [164]:
test = IndeedPaser()
test.parse()

https://www.indeed.fr/jobs?q=developpeur%20docker&l=Lyon


C:\Users\User\Anaconda3\lib\site-packages\ipykernel_launcher.py:109: DeprecationWarning: count is deprecated. Use Collection.count_documents instead.
C:\Users\User\Anaconda3\lib\site-packages\ipykernel_launcher.py:112: DeprecationWarning: count is deprecated. Use Collection.count_documents instead.


aready parsed, skip
page item  https://www.indeed.fr/rc/clk?jk=0a57f689d7a6617d&fccid=ee6a99db163236c2&vjs=3
label - jour count -:  30
saved : https://www.indeed.fr/rc/clk?jk=0a57f689d7a6617d&fccid=ee6a99db163236c2&vjs=3
nan
aready parsed, skip
aready parsed, skip
duplicate url and aready parsed, skip
page item  https://www.indeed.fr/company/Stormshield-SA/jobs/Developpeur-Backend-5abcb03f35e9e046?fccid=327fc972937eb05d&vjs=3


C:\Users\User\Anaconda3\lib\site-packages\ipykernel_launcher.py:106: DeprecationWarning: count is deprecated. Use Collection.count_documents instead.


label - jour count -:  30
saved : https://www.indeed.fr/company/Stormshield-SA/jobs/Developpeur-Backend-5abcb03f35e9e046?fccid=327fc972937eb05d&vjs=3
nan
aready parsed, skip
aready parsed, skip
aready parsed, skip
aready parsed, skip
page item  https://www.indeed.fr/pagead/clk?mo=r&ad=-6NYlbfkN0DNx472i_zaOqC1nCtmTbgeRfOHJF2-3YeEhuwbnpN6gVYCuThEmuBvywyY7Jy6Y9KHol5ZJw7D4lA6zOC2gZNx9uzV_kShlx_QI-rANcPnqQxsRmd5kUaoxIB8l6nF3skj4T6AYHPRX-ExMcgpNCdr8B1qbHxnY23tyNaBwcscrwMkfp1ByV0es6xnBAocrWKFwkBL9OgEW-Y7I6JdxVYFmU7_AHsg4PLm4gE3UU96tHwBbZ-ugfzaD5M5WD131AjCqkyKJNq1RzY8yRDALBMvHp07fxUBZ0-Aj7f6cySleuHk1a8DHIKleHadOcvtf56elkJvK6F63uBIrXFoj6jvFNO9Kb85y2w4sH9FzOC0ReDQz5s5-nOmjf--P8GDE_HfLYT7j9lFumndtxbGmEDCe4Cc6AL55MI7rVfOlsYpzhjdQrXwyUtLBqD4pScZ9sGuyFsQB_ln9qP8xBC29J6QGLp9jeIBL70ahcmB1hKWqz18riMrlt2xSKky_d9LE_A8GvmiQQgwqymqFFxaGc2PRk9HgpGgZs3GkQW2jAZSSXKo04Gmd9ketClNDyBBQbsn4bjN4dGOAfQjyMvZTpVfIRDEHXg6mPo=&p=10&fvj=1&vjs=3
label - jour count -:  15
saved : https://www.indeed.fr/pagead/clk?mo=r&ad=-

...

label - jour count -:  30
saved : https://www.indeed.fr/rc/clk?jk=b95b111225ff9846&fccid=2e9166b9a3b5e00e&vjs=3
nan
aready parsed, skip
aready parsed, skip
aready parsed, skip
aready parsed, skip
aready parsed, skip
aready parsed, skip
aready parsed, skip
aready parsed, skip
page item  https://www.indeed.fr/pagead/clk?mo=r&ad=-6NYlbfkN0DrpjGVQ6ZqR4ukRi4Bazl_S3RUilBZvtfZH4p9MJ8hVmJvCEVulU58J1ppXapc8Aoq2Ph39DRQw_lUzwjofCJQlZeGNcz_bDov9MbvsYs1quuLh9tqB0XXm9umtPIY6en9OWYysoJxVm7SuMNztmjMj-JiGBbu_mS1WLvDGUojTj0NXLe4Na1FDLPs-xc0ZDBZYo8cDQuNiKxMaCeGA9RNPfOpqv2RtdipCEbN_co7a_pYheLjdEuMw2U2HXi_Qf91iYFfa_6SCJ_2Xvc9ePlqfxnpnr9fOh7oRkyaVXdah1iVxG8_sBtFTRhsnJXE1tOmTzaIA6RZca8Ir6Mzw-GTfRSwYGfNJiMhmbJPXR2P9kr3CL5gBZIeTBXYQjFVgxNc-p_qgOBFaWdDNEg22dyT_ijwQ1A_kqAemWwZC7nYQvRwHpFT29wasyaNN2h_nrCVbOd9Dbg3v73eTm6GtFdXx0XoGVc7_HViUIarCL2BsZ7GCWlkQOw0bvboziOQECAZInm24UpeD-IK85HccFh-YAC7ycU99o38N3rTd3CYIO9v1NuByVWZtI6NQ7zUpZ-Rn3AvNKRIoMpztsZVxos4cKHwytUPQMrfDa3cK1R5-nVVaTYke4QU&p=13&fvj=0&vjs=3
label - jour c

label - jour count -:  2
duplicate. archived and skip.
page item  https://www.indeed.fr/pagead/clk?mo=r&ad=-6NYlbfkN0BpfPFFAECyOWxn9I3tUgeAqsh-J7ijxBnxpKsPFbivEybFuAhq0h1OPgjQXd7lk4qKN8841qa5KfliaELov8WLRFUzG_S6v8oYndpbjLXp8NNNey_ebg-afBYi-0WItU8q2Fbxl0H1j0BAft_ILmtQRQN0mFTNntNmYxMPnwF7oNVAZPMPp7kPAJ6mkQ26A9wFGNn3HsntoM488qUpqIN9shap51yLxf5nh4gzsFgQiSwLv7qRwJc3F3J9-lQ3WwOGe_LBdXqsKLgSwYxPN-Ec57Q-fTA7DbWGM_J3NCCbJrfDju1hgAyjtBzfAZr1AFekGTjKfZ0nc0D92t8IMeMf24QVkTcUPmq9skXQtzRLDY4eYjz_ZEUy5SwSYMnOuD12iuMJL4I6z7ZdT4OyZt2uHmWLSO64ZcnKxJguv6wX5n_YeHRvEEHWUAsJK0sXXSVe8NgcTrJRn1YlUHWi8fyL&p=14&fvj=1&vjs=3
label - jour count -:  9
duplicate. archived and skip.
page item  https://www.indeed.fr/pagead/clk?mo=r&ad=-6NYlbfkN0BocCfvWpkQ2s2bFQOXwRrBhUl4DR8RsBm6OzogDHanePjD3sbQZSzd-ZlMLQxHoL7OoFng01UINP9GcIbpMGhwhD64PC4m3eT0JU-tsiEpzoWPil_PC-P1rbLQYOUB2odflGUfkrbDJ2JJZNaPBwuOVmkmAv2x8V8aiLvAKlG6NZ48Ip8QsowJ8bfFch1elpRU5TgN6n1pRlLWazP3jfexllKLmtRFX12g0uisDDzfxtdp87lml79ZveCXhJ_y1BnAO7SR9xGQcomTfGlixFbs

label - jour count -:  9
duplicate. archived and skip.
https://www.indeed.fr/jobs?q=developpeur%20back%20end&l=Nantes
page item  https://www.indeed.fr/pagead/clk?mo=r&ad=-6NYlbfkN0Dzcqu9mB446mMAtcET18noVIRdfBfavQ4Rw9M4fsfZ-fyJDnTeeBOl29quSIUUrHEK4KFp3zAAfMVaGla5LFqemwbQ-P6fQHUlmAFCZQ5VQ77MURjJY4JenY1rfRjq88z6pNP1qhU4fUDDacKRNimGAy2fa0ANO6MBAKRmUN1MVe0BUPd6VKnPt2GO2byKMx0JD_A1pnzBY6QdWZqETAmLvjszq2XJYgN9XdGH10DI1io0PEQn20c_ayyKDhyobEW-NB-mrqwquxbHG2C255UzVihC3_Vl-mcbhP6WjCJClktUskho2WWwQjPdf-nBJaHY4UvNwxxiUrOYap7jJUjHbCAsARJG0cdxlpgN5Lx4QTRufuoaXhLYhI7sBIFKrtRUzprQeIwfdbZ-0ZfGG82IRs_eygEBcPfqH8Dj3iZtOrSMESdZRcwZm-DwL4i-n95LLmAkeWPlfXkzLkfmm8rPfAWu1ju2TwRv4vuR759ue4klopveVehMF0PAtSD177aCTaDiWVadlN8I_Re4xDhPNwRC_hEdJHI9K6UA3g-qz_wB7_Wqo6KT&p=0&fvj=0&vjs=3
label - jour count -:  30
duplicate. archived and skip.
page item  https://www.indeed.fr/pagead/clk?mo=r&ad=-6NYlbfkN0C7yxs162a_2Thx9LKIMPDb2-__MuTZKQn8Y1AQrDlyQeED8bm8yv3N_L9UAgnxvjoH4VYg4OgPekbMWayRi1LTsfCWJQnPQkP4kW3SpFA8Yjn-iqloOabwG

label - jour count -:  8
duplicate. archived and skip.
page item  https://www.indeed.fr/pagead/clk?mo=r&ad=-6NYlbfkN0BocCfvWpkQ2s2bFQOXwRrBhUl4DR8RsBm6OzogDHanePjD3sbQZSzd-ZlMLQxHoL7OoFng01UINP9GcIbpMGhwhD64PC4m3eT0JU-tsiEpzoWPil_PC-P1rbLQYOUB2odflGUfkrbDJ2JJZNaPBwuOVmkmAv2x8V8xZvJZ2voEYR9K6SVTcPdPJ9LFEBAr_RLZ10pr0gdtGKthuYRpWmRdPdqi9cgJ_PTtuIyi5NrrKZrAtuhK7brSb00uwjGIBjhkOVZDR4NDzD91yMef6Ir1AWgdSqXTNPpyGeKUYf8-Z9ssEG2VYsYTsb-q7VvaM5nC2AXGLdMk1ICnk_syP8XJdpfXmcHPP76Mm6CYAIEjncIXqvpSsED6RnzbQe0eBcW2qG6J1nyqS2n5u2t2gEcX0qMIh8WpdRpODhb2Qb3kz76Mr6FvA7BqzaEYGQAxgNxujmBKOo-9mtUhpxK2ETx7&p=3&fvj=1&vjs=3
label - jour count -:  30
duplicate. archived and skip.
aready parsed, skip
aready parsed, skip
aready parsed, skip
aready parsed, skip
aready parsed, skip
page item  https://www.indeed.fr/rc/clk?jk=dd0c57e993785254&fccid=47fb73a3ab3ea34a&vjs=3
label - jour count -:  2
saved : https://www.indeed.fr/rc/clk?jk=dd0c57e993785254&fccid=47fb73a3ab3ea34a&vjs=3
nan
aready parsed, skip
page item  https

KeyboardInterrupt: 

In [169]:
dao = IndeedMongodbDao()
data = dao.get_all_data()
df = pd.DataFrame(list(data))
df.to_csv("indeed_mongo.csv")